In [11]:
import numpy as np
import pandas as pd
from pandas.tseries.offsets import Hour, Minute
from pandas.tseries.offsets import Day, MonthEnd
from pandas.tseries.offsets import Hour
from sklearn.model_selection import TimeSeriesSplit
from sklearn.preprocessing import MinMaxScaler
from sklearn.metrics import mean_squared_error as mse
from sklearn.model_selection import RandomizedSearchCV
from keras.preprocessing.sequence import TimeseriesGenerator
from time import time
import xgboost as xgb

np.random.seed(77)


In [12]:

global busses
busses = ['309_WIND_1', '317_WIND_1', '303_WIND_1', '122_WIND_1']
df = pd.read_csv('Wind_deseason_15.csv', parse_dates=[0], index_col=0)



In [13]:
def lags(df, n):
    
    df_new = df
    
    for i in range(n):
        name = "lag "+ str(i+1)
        df_new[name] = df['309_WIND_1'].shift(i+1)
    
    return df_new
    

In [14]:
def TrainTest(df):
    
    num_rows = df.shape[0]
    
    num_training = (num_rows * 8)//10
   
    #train = df.iloc[0:num_training]
    #test = df.iloc[num_training:num_rows]
    
    
    return num_training 

In [15]:
def TestModel(X,test, mod):
    
    MSEs = []
    
    for i in range(len(X)):
        
        print(X.iloc[i].to_frame().transpose())
        pred = mod.predict(X.iloc[i].to_frame().transpose())
        #pred = scaler.inverse_transform(pred)
        
        print(pred)
        print(test.iloc[i])
        
        MSEs.append(mse([test.iloc[i]],pred))
        
        
    return MSEs

In [16]:
#def model1Train(X_train,Y_train,X_test,Y_test):
   


In [17]:
def model2Train(X_train,Y_train):
    params = {'eta' : [0.001, 0.01, 0.1, 0.25, 0.3, 0.4, 0.5, 0.8],
              'gamma' : [0, 1, 2, 3, 4, 5, 10, 20, 40, 80, 100],
              'max_depth' : [2, 3, 4, 5, 6, 7, 8, 9, 10],
              'min_child_weight' : [0,1, 2, 3, 4, 5, 10, 20, 40, 80, 100],
              'max_delta_step' : [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]} 
    mod = xgb.XGBRegressor()
    rand = RandomizedSearchCV(mod, param_distributions = params, n_iter = 15, n_jobs = -1, verbose = True, random_state = 40)
    start = time()
    rand.fit(X_train, Y_train)#keep low for now, edit later eval_set = [(X_train, y_train),(X_test, y_test)]
    print('time')
    print(time()-start)
    params = rand.best_params_
    
    return rand, params

In [18]:
def runModels(df, last):
    scaler = MinMaxScaler()
     
    bound = TrainTest(df)
    
    
    last_index =pd.DatetimeIndex(data = [idx.replace(year = 2019) for idx in last.index])
    df_index = df.index
    new_df_idx = last_index.append(df_index)
    
    array_df = df['309_WIND_1'].to_numpy()
    
    array_df = np.append(last['309_WIND_1'].to_numpy(), array_df)
    
    
    
    new_df = pd.DataFrame(array_df, columns = ['309_WIND_1'])
    new_df['Dates'] = new_df_idx
    new_df = new_df.set_index('Dates')
    

    
    
    lag = lags(new_df, 107)
    
    lag = lag[lag.columns[::-1]]
    

    
    
    lagged_train = lag.iloc[107:bound+107]
    lagged_test = lag.iloc[bound+107:]

    X_train = lagged_train.drop('309_WIND_1', axis = 1)
    Y_train = lagged_train['309_WIND_1']
    
    X_test = lagged_test.drop('309_WIND_1', axis = 1)
    Y_test = lagged_test['309_WIND_1']
    
    print(X_train)
    print(X_test)
  
    
    #mod = model1Train(X_train, Y_train,X_test, Y_test)
    mod, params = model2Train(X_train, Y_train)
    
    Tests = TestModel(X_test, Y_test, mod)
    
    print(Tests)
    
    return Tests, params

    
    

In [19]:

df1 = df[df.index.month.isin([1,2,3])]
df2 = df[df.index.month.isin([4,5,6])]
df3 = df[df.index.month.isin([7,8,9])]
df4 = df[df.index.month.isin([10,11,12])]

In [ ]:
mse1, param1 = runModels(df1,df4.iloc[-107:])

C:\Users\bvits\AppData\Local\Temp\ipykernel_26656\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_26656\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_26656\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider

                       lag 107    lag 106    lag 105    lag 104    lag 103  \
Dates                                                                        
2020-01-01 00:15:00  40.448957  34.680895  17.846166  32.878104  59.010041   
2020-01-01 00:30:00  34.680895  17.846166  32.878104  59.010041  43.241979   
2020-01-01 00:45:00  17.846166  32.878104  59.010041  43.241979  28.607250   
2020-01-01 01:00:00  32.878104  59.010041  43.241979  28.607250  -0.694145   
2020-01-01 01:15:00  59.010041  43.241979  28.607250  -0.694145 -18.362208   
...                        ...        ...        ...        ...        ...   
2020-03-13 18:00:00  90.941599  94.979552  93.750838  94.255458  90.360077   
2020-03-13 18:15:00  94.979552  93.750838  94.255458  90.360077  82.598030   
2020-03-13 18:30:00  93.750838  94.255458  90.360077  82.598030  78.769316   
2020-03-13 18:45:00  94.255458  90.360077  82.598030  78.769316  72.473935   
2020-03-13 19:00:00  90.360077  82.598030  78.769316  72.473935 

In [11]:
mse2, param2 = runModels(df2,df1.iloc[-107:])

C:\Users\bvits\AppData\Local\Temp\ipykernel_25268\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_25268\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_25268\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider

                        lag 107     lag 106     lag 105     lag 104  \
Dates                                                                 
2020-04-01 00:00:00  -26.473888  -25.536000  -20.331446  -19.326892   
2020-04-01 00:15:00  -25.536000  -20.331446  -19.326892  -18.455672   
2020-04-01 00:30:00  -20.331446  -19.326892  -18.455672  -19.117784   
2020-04-01 00:45:00  -19.326892  -18.455672  -19.117784  -23.179897   
2020-04-01 01:00:00  -18.455672  -19.117784  -23.179897  -24.875343   
...                         ...         ...         ...         ...   
2020-06-12 17:45:00  100.220067  107.687854  109.888974  116.456761   
2020-06-12 18:00:00  107.687854  109.888974  116.456761  121.091214   
2020-06-12 18:15:00  109.888974  116.456761  121.091214  123.092334   
2020-06-12 18:30:00  116.456761  121.091214  123.092334  126.993454   
2020-06-12 18:45:00  121.091214  123.092334  126.993454  127.061241   

                        lag 103     lag 102     lag 101     lag 100  \
Dates

                        lag 107     lag 106     lag 105     lag 104  \
2020-06-12 19:00:00  123.092334  126.993454  127.061241  128.529028   

                        lag 103     lag 102     lag 101     lag 100  \
2020-06-12 19:00:00  127.330148  128.664601  128.365721  127.966841   

                         lag 99      lag 98  ...     lag 10      lag 9  \
2020-06-12 19:00:00  127.701295  128.002415  ... -21.405391 -21.270938   

                         lag 8      lag 7      lag 6      lag 5      lag 4  \
2020-06-12 19:00:00 -21.269818 -21.702031 -21.200911 -20.499791 -18.332004   

                         lag 3      lag 2      lag 1  
2020-06-12 19:00:00 -18.497551 -18.963097 -20.461977  

[1 rows x 107 columns]
[-19.720823]
-20.89419052438829
                        lag 107     lag 106     lag 105     lag 104  \
2020-06-12 19:15:00  126.993454  127.061241  128.529028  127.330148   

                        lag 103     lag 102     lag 101     lag 100  \
2020-06-12 19:15:00  128.664

[-21.1133]
-21.011842842533746
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-12 22:45:00  60.475802  44.743589  30.311376  21.712496  19.880282   

                      lag 102   lag 101    lag 100     lag 99     lag 98  ...  \
2020-06-12 22:45:00  7.181402 -5.884144 -12.349691 -16.381904 -17.414117  ...   

                        lag 10      lag 9      lag 8     lag 7      lag 6  \
2020-06-12 22:45:00 -20.655257 -21.254137 -21.019683 -20.68523 -21.717443   

                        lag 5     lag 4      lag 3      lag 2      lag 1  
2020-06-12 22:45:00 -21.48299 -21.28187 -21.314083 -21.212963 -21.011843  

[1 rows x 107 columns]
[-19.094837]
-17.044056103353654
                       lag 107    lag 106    lag 105    lag 104   lag 103  \
2020-06-12 23:00:00  44.743589  30.311376  21.712496  19.880282  7.181402   

                      lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-12 23:00:00 -5.884144 -12.349691 -16.381904 -17

[-11.19524]
-11.47369828407404
                       lag 107   lag 106    lag 105   lag 104   lag 103  \
2020-06-13 02:15:00 -16.208517 -13.34073 -11.212649 -6.811529 -5.877076   

                      lag 102   lag 101   lag 100     lag 99     lag 98  ...  \
2020-06-13 02:15:00  1.890711  4.525164  8.859618  15.960738  23.861858  ...   

                        lag 10     lag 9     lag 8     lag 7     lag 6  \
2020-06-13 02:15:00 -16.072909 -1.149326 -2.481539 -6.547085 -7.479299   

                        lag 5     lag 4     lag 3      lag 2      lag 1  
2020-06-13 02:15:00 -7.144845 -8.043725 -8.609272 -11.141485 -11.473698  

[1 rows x 107 columns]
[-11.910867]
-12.272578211560624
                      lag 107    lag 106   lag 105   lag 104   lag 103  \
2020-06-13 02:30:00 -13.34073 -11.212649 -6.811529 -5.877076  1.890711   

                      lag 102   lag 101    lag 100     lag 99     lag 98  ...  \
2020-06-13 02:30:00  4.525164  8.859618  15.960738  23.861858  26.729645 

...

[-15.30757]
-17.034774689284358
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 08:30:00 -0.612827 -3.878867  1.021759  0.155719  3.823012   

                      lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-06-30 08:30:00  1.490306 -7.209068 -8.075108 -9.274481 -9.607188  ...   

                       lag 10     lag 9     lag 8     lag 7      lag 6  \
2020-06-30 08:30:00  7.959585  2.426879  1.094172 -1.738535 -10.371241   

                        lag 5      lag 4      lag 3      lag 2      lag 1  
2020-06-30 08:30:00 -7.137281 -12.203321 -15.602695 -15.402068 -17.034775  

[1 rows x 107 columns]
[-17.453176]
-16.734148040363973
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 08:45:00 -3.878867  1.021759  0.155719  3.823012  1.490306   

                      lag 102   lag 101   lag 100    lag 99     lag 98  ...  \
2020-06-30 08:45:00 -7.209068 -8.075108 -9.274481 -9.607188 -11.773228  ...   



[-18.96385]
-18.859334937732307
                       lag 107    lag 106   lag 105    lag 104    lag 103  \
2020-06-30 12:00:00 -12.470721 -11.836761 -9.636134 -11.135508 -14.168214   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 12:00:00 -13.600921 -13.466961 -16.233001 -16.232375 -16.665081   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 12:00:00  ... -18.598308 -18.764348 -18.930388 -18.663095   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 12:00:00 -19.162468 -18.728508 -18.994548 -18.893922 -18.826628   

                         lag 1  
2020-06-30 12:00:00 -18.859335  

[1 rows x 107 columns]
[-18.96385]
-18.892041622145257
                       lag 107   lag 106    lag 105    lag 104    lag 103  \
2020-06-30 12:15:00 -11.836761 -9.636134 -11.135508 -14.168214 -13.600921   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \

[-17.66234]
-16.98389518618026
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 15:30:00 -18.695281 -18.361321 -18.260695 -18.593401 -18.492775   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 15:30:00 -18.558815 -18.658188 -18.390895 -18.590268 -18.389641   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 15:30:00  ... -18.756202 -18.955575 -18.921615 -18.687655   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 15:30:00 -18.987028 -18.586402 -17.919108 -17.851815 -17.451189   

                         lag 1  
2020-06-30 15:30:00 -16.983895  

[1 rows x 107 columns]
[-17.66234]
-16.983268537259875
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 15:45:00 -18.361321 -18.260695 -18.593401 -18.492775 -18.558815   

                       lag 102    lag 101    lag 100     lag 99     lag 98

[-11.325154]
-10.041162119041156
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 19:15:00 -18.552548 -18.518588 -18.217962 -18.117335 -18.350042   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 19:15:00 -18.449415 -18.448788 -18.181495 -18.214202 -18.280242   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 19:15:00  ... -14.413469 -13.812842 -13.078882 -12.978255   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 19:15:00 -12.344295 -11.977002 -11.143042 -10.342415 -10.541789   

                         lag 1  
2020-06-30 19:15:00 -10.041162  

[1 rows x 107 columns]
[-11.325154]
-8.90720213678744
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 19:30:00 -18.518588 -18.217962 -18.117335 -18.350042 -18.449415   

                       lag 102    lag 101    lag 100     lag 99     lag 9

[3.8515058]
-2.29905570082244
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 22:45:00 -18.110442 -17.876482 -16.575855 -16.608562 -16.207935   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 22:45:00 -16.673975 -16.306682 -16.472722 -17.338762 -16.638135   

                     ...    lag 10     lag 9     lag 8     lag 7      lag 6  \
2020-06-30 22:45:00  ... -7.471362 -6.804069 -6.003442 -4.336149  18.397811   

                         lag 5     lag 4     lag 3     lag 2     lag 1  
2020-06-30 22:45:00  13.331771 -1.300936 -7.933642 -0.333016 -2.299056  

[1 rows x 107 columns]
[-2.0950298]
-14.13176238523539
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 23:00:00 -17.876482 -16.575855 -16.608562 -16.207935 -16.673975   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 23:00:00 -16.306682 -16.472722 -17.338762 -16.638

In [12]:
mse3, param3 = runModels(df2,df.iloc[-107:])

                        lag 107     lag 106     lag 105     lag 104  \
Dates                                                                 
2020-04-01 00:00:00   34.680895   17.846166   32.878104   59.010041   
2020-04-01 00:15:00   17.846166   32.878104   59.010041   43.241979   
2020-04-01 00:30:00   32.878104   59.010041   43.241979   28.607250   
2020-04-01 00:45:00   59.010041   43.241979   28.607250   -0.694145   
2020-04-01 01:00:00   43.241979   28.607250   -0.694145  -18.362208   
...                         ...         ...         ...         ...   
2020-06-12 17:45:00  100.220067  107.687854  109.888974  116.456761   
2020-06-12 18:00:00  107.687854  109.888974  116.456761  121.091214   
2020-06-12 18:15:00  109.888974  116.456761  121.091214  123.092334   
2020-06-12 18:30:00  116.456761  121.091214  123.092334  126.993454   
2020-06-12 18:45:00  121.091214  123.092334  126.993454  127.061241   

                        lag 103     lag 102     lag 101     lag 100  \
Dates

C:\Users\bvits\AppData\Local\Temp\ipykernel_25268\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_25268\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_25268\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider

                        lag 107     lag 106     lag 105     lag 104  \
Dates                                                                 
2020-06-12 19:00:00  123.092334  126.993454  127.061241  128.529028   
2020-06-12 19:15:00  126.993454  127.061241  128.529028  127.330148   
2020-06-12 19:30:00  127.061241  128.529028  127.330148  128.664601   
2020-06-12 19:45:00  128.529028  127.330148  128.664601  128.365721   
2020-06-12 20:00:00  127.330148  128.664601  128.365721  127.966841   
...                         ...         ...         ...         ...   
2020-06-30 22:45:00  -18.110442  -17.876482  -16.575855  -16.608562   
2020-06-30 23:00:00  -17.876482  -16.575855  -16.608562  -16.207935   
2020-06-30 23:15:00  -16.575855  -16.608562  -16.207935  -16.673975   
2020-06-30 23:30:00  -16.608562  -16.207935  -16.673975  -16.306682   
2020-06-30 23:45:00  -16.207935  -16.673975  -16.306682  -16.472722   

                        lag 103     lag 102     lag 101     lag 100  \
Dates

[-21.603779]
-21.21296291504716
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-12 22:30:00  81.008015  60.475802  44.743589  30.311376  21.712496   

                       lag 102   lag 101   lag 100     lag 99     lag 98  ...  \
2020-06-12 22:30:00  19.880282  7.181402 -5.884144 -12.349691 -16.381904  ...   

                        lag 10      lag 9      lag 8      lag 7     lag 6  \
2020-06-12 22:30:00 -20.756377 -20.655257 -21.254137 -21.019683 -20.68523   

                         lag 5     lag 4     lag 3      lag 2      lag 1  
2020-06-12 22:30:00 -21.717443 -21.48299 -21.28187 -21.314083 -21.212963  

[1 rows x 107 columns]
[-21.603779]
-21.011842842533746
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-12 22:45:00  60.475802  44.743589  30.311376  21.712496  19.880282   

                      lag 102   lag 101    lag 100     lag 99     lag 98  ...  \
2020-06-12 22:45:00  7.181402 -5.884144 -12.3496

[-5.695628]
-11.141485023254132
                      lag 107    lag 106   lag 105    lag 104   lag 103  \
2020-06-13 02:00:00 -16.44297 -16.208517 -13.34073 -11.212649 -6.811529   

                      lag 102   lag 101   lag 100    lag 99     lag 98  ...  \
2020-06-13 02:00:00 -5.877076  1.890711  4.525164  8.859618  15.960738  ...   

                        lag 10      lag 9     lag 8     lag 7     lag 6  \
2020-06-13 02:00:00 -17.107363 -16.072909 -1.149326 -2.481539 -6.547085   

                        lag 5     lag 4     lag 3     lag 2      lag 1  
2020-06-13 02:00:00 -7.479299 -7.144845 -8.043725 -8.609272 -11.141485  

[1 rows x 107 columns]
[-10.134301]
-11.47369828407404
                       lag 107   lag 106    lag 105   lag 104   lag 103  \
2020-06-13 02:15:00 -16.208517 -13.34073 -11.212649 -6.811529 -5.877076   

                      lag 102   lag 101   lag 100     lag 99     lag 98  ...  \
2020-06-13 02:15:00  1.890711  4.525164  8.859618  15.960738  23.861858  .

...

[-19.358496]
-18.932268093602826
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 09:30:00  3.823012  1.490306 -7.209068 -8.075108 -9.274481   

                      lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 09:30:00 -9.607188 -11.773228 -12.039268 -14.271974 -13.171348   

                     ...     lag 10     lag 9      lag 8      lag 7  \
2020-06-30 09:30:00  ... -10.371241 -7.137281 -12.203321 -15.602695   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 09:30:00 -15.402068 -17.034775 -16.734148 -17.833521 -18.932895   

                         lag 1  
2020-06-30 09:30:00 -18.932268  

[1 rows x 107 columns]
[-19.358496]
-18.598308111349105
                      lag 107   lag 106   lag 105   lag 104   lag 103  \
2020-06-30 09:45:00  1.490306 -7.209068 -8.075108 -9.274481 -9.607188   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 09:45:

[-18.565176]
-18.490161675384105
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 13:00:00 -14.168214 -13.600921 -13.466961 -16.233001 -16.232375   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 13:00:00 -16.665081 -16.564455 -17.363828 -17.463201 -17.695908   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 13:00:00  ... -19.162468 -18.728508 -18.994548 -18.893922   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 13:00:00 -18.826628 -18.859335 -18.892042 -18.924748 -19.057455   

                         lag 1  
2020-06-30 13:00:00 -18.490162  

[1 rows x 107 columns]
[-17.870466]
-18.756201693130382
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 13:15:00 -13.600921 -13.466961 -16.233001 -16.232375 -16.665081   

                       lag 102    lag 101    lag 100     lag 99     lag

[-15.631928]
-15.682015239419105
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 16:15:00 -18.593401 -18.492775 -18.558815 -18.658188 -18.390895   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 16:15:00 -18.590268 -18.389641 -18.322348 -18.288388 -18.687762   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 16:15:00  ... -18.687655 -18.987028 -18.586402 -17.919108   

                         lag 6      lag 5      lag 4      lag 3      lag 2  \
2020-06-30 16:15:00 -17.851815 -17.451189 -16.983895 -16.983269 -15.849309   

                         lag 1  
2020-06-30 16:15:00 -15.682015  

[1 rows x 107 columns]
[-14.56361]
-15.24805525716539
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 16:30:00 -18.492775 -18.558815 -18.658188 -18.390895 -18.590268   

                       lag 102    lag 101    lag 100     lag 99     lag 9

[-8.568134]
-8.773242154533726
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 19:45:00 -18.217962 -18.117335 -18.350042 -18.449415 -18.448788   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 19:45:00 -18.181495 -18.214202 -18.280242 -17.579615 -18.012322   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-06-30 19:45:00  ... -13.078882 -12.978255 -12.344295 -11.977002   

                         lag 6      lag 5      lag 4      lag 3     lag 2  \
2020-06-30 19:45:00 -11.143042 -10.342415 -10.541789 -10.041162 -8.907202   

                        lag 1  
2020-06-30 19:45:00 -8.773242  

[1 rows x 107 columns]
[-5.178832]
-8.339282172280004
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 20:00:00 -18.117335 -18.350042 -18.449415 -18.448788 -18.181495   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2

[-16.103601]
-17.99717575406129
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 23:30:00 -16.608562 -16.207935 -16.673975 -16.306682 -16.472722   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 23:30:00 -17.338762 -16.638135 -16.504175 -16.436882 -15.502922   

                     ...    lag 10      lag 9      lag 8     lag 7     lag 6  \
2020-06-30 23:30:00  ... -4.336149  18.397811  13.331771 -1.300936 -7.933642   

                        lag 5     lag 4      lag 3      lag 2      lag 1  
2020-06-30 23:30:00 -0.333016 -2.299056 -14.131762 -16.931136 -17.997176  

[1 rows x 107 columns]
[-17.473936]
-12.063215771807569
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-06-30 23:45:00 -16.207935 -16.673975 -16.306682 -16.472722 -17.338762   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-06-30 23:45:00 -16.638135 -16.504175 -16.43688

In [13]:
mse4, param4 = runModels(df4,df3.iloc[-107:])

                       lag 107    lag 106    lag 105    lag 104    lag 103  \
Dates                                                                        
2020-10-01 00:00:00 -24.529253 -24.297302 -24.998685 -24.466735 -24.668118   
2020-10-01 00:15:00 -24.297302 -24.998685 -24.466735 -24.668118 -24.502834   
2020-10-01 00:30:00 -24.998685 -24.466735 -24.668118 -24.502834 -24.404217   
2020-10-01 00:45:00 -24.466735 -24.668118 -24.502834 -24.404217 -24.672267   
2020-10-01 01:00:00 -24.668118 -24.502834 -24.404217 -24.672267 -24.406983   
...                        ...        ...        ...        ...        ...   
2020-12-13 13:00:00 -36.091985 -35.993458 -35.961597 -36.296402 -35.964541   
2020-12-13 13:15:00 -35.993458 -35.961597 -36.296402 -35.964541 -35.632680   
2020-12-13 13:30:00 -35.961597 -36.296402 -35.964541 -35.632680 -36.134153   
2020-12-13 13:45:00 -36.296402 -35.964541 -35.632680 -36.134153 -35.968958   
2020-12-13 14:00:00 -35.964541 -35.632680 -36.134153 -35.968958 

C:\Users\bvits\AppData\Local\Temp\ipykernel_25268\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_25268\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df_new[name] = df['309_WIND_1'].shift(i+1)
C:\Users\bvits\AppData\Local\Temp\ipykernel_25268\1454027626.py:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider

                      lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-12-13 14:15:00 -35.63268 -36.134153 -35.968958 -36.037097 -34.271903   

                       lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-12-13 14:15:00 -33.973375 -33.774848 -34.642987 -35.544459 -35.845931   

                     ...    lag 10      lag 9     lag 8      lag 7      lag 6  \
2020-12-13 14:15:00  ... -27.28621 -27.321003 -27.08913 -27.157257 -27.158717   

                         lag 5      lag 4      lag 3     lag 2      lag 1  
2020-12-13 14:15:00 -26.960177 -20.694971 -18.929764 -8.497891  24.267315  

[1 rows x 107 columns]
[46.05369]
71.39918819741972
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-12-13 14:30:00 -36.134153 -35.968958 -36.037097 -34.271903 -33.973375   

                       lag 102    lag 101    lag 100     lag 99    lag 98  \
2020-12-13 14:30:00 -33.774848 -34.642987 -35.544459 -35.845931 -35.61407   

        

[116.663826]
115.48020521180791
                       lag 107    lag 106    lag 105   lag 104    lag 103  \
2020-12-13 17:45:00 -25.953293 -25.654765 -23.989571 -20.95771 -20.959182   

                       lag 102   lag 101    lag 100     lag 99     lag 98  \
2020-12-13 17:45:00 -17.527321 -15.79546 -14.630266 -11.398405 -11.599877   

                     ...      lag 10       lag 9       lag 8       lag 7  \
2020-12-13 17:45:00  ...  114.260014  116.791887  118.457093  118.088967   

                          lag 6       lag 5       lag 4       lag 3  \
2020-12-13 17:45:00  119.587506  118.919379  116.351253  117.849792   

                          lag 2       lag 1  
2020-12-13 17:45:00  116.481665  115.480205  

[1 rows x 107 columns]
[117.64217]
116.1787449821455
                       lag 107    lag 106   lag 105    lag 104    lag 103  \
2020-12-13 18:00:00 -25.654765 -23.989571 -20.95771 -20.959182 -17.527321   

                      lag 102    lag 101    lag 100     lag 9

[112.210106]
103.69455555952948
                      lag 107   lag 106   lag 105  lag 104   lag 103  \
2020-12-13 21:00:00 -3.872433 -1.807239 -0.242045  2.42315  3.955011   

                      lag 102   lag 101    lag 100     lag 99     lag 98  ...  \
2020-12-13 21:00:00  5.886872  8.452066  10.283927  11.949121  14.080982  ...   

                         lag 10       lag 9       lag 8      lag 7      lag 6  \
2020-12-13 21:00:00  109.941031  103.206237  106.071444  105.13665  111.73519   

                          lag 5       lag 4       lag 3       lag 2  \
2020-12-13 21:00:00  109.800396  103.265603  104.730809  111.029349   

                          lag 1  
2020-12-13 21:00:00  103.694556  

[1 rows x 107 columns]
[94.990845]
92.55976199653372
                      lag 107   lag 106  lag 105   lag 104   lag 103  \
2020-12-13 21:15:00 -1.807239 -0.242045  2.42315  3.955011  5.886872   

                      lag 102    lag 101    lag 100     lag 99    lag 98  ...  \
2020-1

...

[10.128903]
11.514092354929828
                      lag 107   lag 106   lag 105    lag 104    lag 103  \
2020-12-31 07:30:00 -6.725602 -4.460331  5.504941  23.170212  26.968816   

                       lag 102    lag 101    lag 100   lag 99     lag 98  ...  \
2020-12-31 07:30:00  24.834087  30.066025  37.164629  50.7299  46.161838  ...   

                        lag 10      lag 9      lag 8      lag 7     lag 6  \
2020-12-31 07:30:00  51.193319  20.891924  21.723861  33.422466  41.72107   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-12-31 07:30:00  43.553008  24.384946  18.716884  13.815488  11.514092  

[1 rows x 107 columns]
[10.966878]
13.81269677842951
                      lag 107   lag 106    lag 105    lag 104    lag 103  \
2020-12-31 07:45:00 -4.460331  5.504941  23.170212  26.968816  24.834087   

                       lag 102    lag 101  lag 100     lag 99     lag 98  ...  \
2020-12-31 07:45:00  30.066025  37.164629  50.7299  46.161

[-30.992054]
-31.53877904940808
                      lag 107    lag 106    lag 105  lag 104   lag 103  \
2020-12-31 11:00:00  22.45486  18.453465  10.685402  2.71734 -1.917389   

                      lag 102  lag 101   lag 100    lag 99    lag 98  ...  \
2020-12-31 11:00:00 -1.352118  3.67982 -0.921575 -0.256304 -3.124367  ...   

                        lag 10      lag 9      lag 8     lag 7     lag 6  \
2020-12-31 11:00:00  41.473781  40.872386  20.537657  5.469594  4.134865   

                        lag 5      lag 4      lag 3      lag 2      lag 1  
2020-12-31 11:00:00 -8.999863 -21.667926 -30.469321 -31.970717 -31.538779  

[1 rows x 107 columns]
[-37.77517]
-31.4401746259084
                       lag 107    lag 106  lag 105   lag 104   lag 103  \
2020-12-31 11:15:00  18.453465  10.685402  2.71734 -1.917389 -1.352118   

                     lag 102   lag 101   lag 100    lag 99    lag 98  ...  \
2020-12-31 11:15:00  3.67982 -0.921575 -0.256304 -3.124367  4.274238  ...   

 

[-34.5268]
-31.95692154391232
                      lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-12-31 14:15:00  7.170051  11.568656  23.133927  28.965864  24.364469   

                      lag 102   lag 101    lag 100     lag 99     lag 98  ...  \
2020-12-31 14:15:00  9.396407 -7.104989 -21.906385 -28.774447 -29.275842  ...   

                        lag 10      lag 9      lag 8      lag 7      lag 6  \
2020-12-31 14:15:00 -32.211028 -32.645757 -32.013819 -32.415215 -32.383277   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-12-31 14:15:00 -32.418006 -32.352735 -32.487464 -32.288859 -31.956922  

[1 rows x 107 columns]
[-32.215282]
-32.458317120412644
                       lag 107    lag 106    lag 105    lag 104   lag 103  \
2020-12-31 14:30:00  11.568656  23.133927  28.965864  24.364469  9.396407   

                      lag 102    lag 101    lag 100     lag 99     lag 98  \
2020-12-31 14:30:00 -7.104989 -21.906385 -28.774447 

[-31.92114]
-32.04165473020056
                      lag 107   lag 106    lag 105    lag 104   lag 103  \
2020-12-31 17:30:00 -3.348091 -15.98282 -23.650883 -20.885611 -23.12034   

                       lag 102    lag 101   lag 100     lag 99     lag 98  \
2020-12-31 17:30:00 -22.455069 -24.523131 -22.55786 -22.259256 -26.227318   

                     ...     lag 10      lag 9      lag 8      lag 7  \
2020-12-31 17:30:00  ... -32.029171 -32.097233 -32.598619 -32.466672   

                         lag 6      lag 5     lag 4      lag 3      lag 2  \
2020-12-31 17:30:00 -32.168058 -32.702777 -32.47083 -32.705549 -32.540269   

                         lag 1  
2020-12-31 17:30:00 -32.041655  

[1 rows x 107 columns]
[-31.162016]
-32.74304080984055
                      lag 107    lag 106    lag 105   lag 104    lag 103  \
2020-12-31 17:45:00 -15.98282 -23.650883 -20.885611 -23.12034 -22.455069   

                       lag 102   lag 101    lag 100     lag 99     lag 98  \
2020-12-31 

[-29.427511]
-32.4763067212004
                       lag 107    lag 106    lag 105    lag 104    lag 103  \
2020-12-31 23:45:00  30.517019  40.448957  34.680895  17.846166  32.878104   

                       lag 102    lag 101   lag 100    lag 99     lag 98  ...  \
2020-12-31 23:45:00  59.010041  43.241979  28.60725 -0.694145 -18.362208  ...   

                        lag 10      lag 9      lag 8      lag 7      lag 6  \
2020-12-31 23:45:00 -32.697165 -32.631885 -31.999937 -32.634657 -32.836043   

                         lag 5      lag 4      lag 3      lag 2      lag 1  
2020-12-31 23:45:00 -32.537429 -32.738815 -32.440201 -32.908254 -32.476307  

[1 rows x 107 columns]
[-29.187456]
-32.67769280084039
[642.3941843866993, 469.0144231971811, 54.899381132425525, 51.968188127748505, 42.929584175199665, 55.33152597426207, 58.69484478107146, 24.305506990178948, 28.673171209131812, 7.062025040104657, 0.8166821032233506, 9.324590475701148, 0.15023580366250358, 1.4009581436552243, 2.1416

In [14]:
print('season 1')


print(param1)



season 1
{'min_child_weight': 5, 'max_depth': 4, 'max_delta_step': 5, 'gamma': 40, 'eta': 0.5}


In [15]:
print('season 1')

\
print(param2)


season 1
{'min_child_weight': 5, 'max_depth': 4, 'max_delta_step': 5, 'gamma': 40, 'eta': 0.5}


In [16]:
print('season 1')


print(param3)



season 1
{'min_child_weight': 80, 'max_depth': 5, 'max_delta_step': 3, 'gamma': 2, 'eta': 0.8}


In [17]:
print('season 1')


print(param4)


season 1
{'min_child_weight': 5, 'max_depth': 4, 'max_delta_step': 5, 'gamma': 40, 'eta': 0.5}


In [18]:
d = {'Season 1':mse1,'Season 2':mse2,'Season 3':mse3,'Season 4':mse4}
df_errors_GBDT = pd.DataFrame({k:pd.Series(v) for k,v in d.items()})

df_errors_GBDT.to_csv('GBDT_errors_random.csv')
